<a href="https://colab.research.google.com/github/CodeCraftIA/scrape_adebooks/blob/main/books_scraping.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Main project scrape Adebooks data points given adebooks urls

In [ ]:
import requests
from bs4 import BeautifulSoup
from tqdm import tqdm
import pandas as pd
import re
import time

# Create empty lists to store data
titles = []
authors = []
isbn13s = []
prices = []
publishers = []
years = []
bindings = []
image_links = []


def extract_lines(input_file_path, start_line, end_line, output_file_path):
    try:
        with open(input_file_path, 'r') as input_file, open(output_file_path, 'w') as output_file:
            lines = input_file.readlines()
            # Adjusting start_line and end_line to be within the valid range
            start_line = max(1, min(start_line, len(lines)))
            end_line = max(start_line, min(end_line, len(lines)))

            # Writing the selected lines to the output file
            output_file.writelines(lines[start_line - 1:end_line])

        print(f"Lines {start_line} to {end_line} extracted and saved to {output_file_path}")

    except Exception as e:
        print(f"Error: {e}")

def check_results(url):
  with open('errors.txt', 'a') as file_er:
    try:
        headers = {"User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/124.0.0.0 Safari/537.36"}
        response = requests.get(url, headers=headers)

        if not response.ok:
            print('Status Code:', response.status_code)
            raise Exception('Failed to fetch')

        soup = BeautifulSoup(response.text, 'html.parser')
        ul = soup.find('ul', id="srp-results")
        if not ul:
          time.sleep(0.6)
          return
        li = ul.find_all('li', class_="cf result-item")
        for temp in li:
            title=""
            author=""
            isbn13=""
            price=""
            publisher=""
            year=""
            binding=""
            image_link=""
            isbn_data = temp.find('p', class_="isbn pub-data")
            if isbn_data:
                isbn13 = isbn_data.find('span', class_="pl-md")
                if isbn13:
                    isbn13 = isbn13.text.strip()
                    isbn13 = isbn13.replace('ISBN 13: ', '')
            if isbn13=="":
                continue


            title = temp.find('h2', class_="title")
            if title:
                title = title.text.strip()
            author = temp.find('p', class_="author")
            if author:
                author = author.text.strip()

            price = temp.find('p', class_="item-price")
            if price:
                # Extract the numerical part of the price and convert it to an integer
                price = int(re.search(r'\d+', price.text.strip().replace(",", "")).group())

            publish_data = temp.find('p', class_="text-secondary pub-data")
            if publish_data:
                publisher = publish_data.find('span', class_="opt-publisher")
                if publisher:
                    publisher = publisher.text.strip()
                    publisher = publisher.replace(",", "")
                year = publish_data.find('span', class_="opt-publish-date")
                if year:
                    year = year.text.strip()
            binding_div = temp.find('div', class_="buy-box-data col-xs-4")
            if binding_div:
                binding_p = binding_div.find('p', class_="item-meta-data")
                if binding_p:
                    binding = binding_p.find('span', attrs={'data-cy': 'listing-book-condition'})
                    if binding:
                        binding = binding.text.strip()
                        if "Hardcover" in binding:
                          binding= "Hardcover"
                        elif "Softcover" in binding:
                          binding= "Softcover"
                        else:
                          binding=""
            img_tag = temp.find('img', class_='srp-item-image')
            if img_tag:
                image_link = img_tag['src']
            titles.append(title)
            authors.append(author)
            isbn13s.append(isbn13)
            prices.append(str(price))
            publishers.append(publisher)
            years.append(year)
            bindings.append(binding)
            image_links.append(image_link)
    except Exception as e:
      print("Error on URL:", url, "Error:", e)
      file_er.write(url +'\n')
      time.sleep(1)


extract_lines('Top1000.txt', 210501, 212600, 'file.txt')

# Read URLs from file
with open('file.txt', 'r') as file:
    urls = file.readlines()

for url in tqdm(urls):
    url = url.strip()  # Remove leading/trailing whitespace and newline characters
    check_results(url)


# Create DataFrame
df = pd.DataFrame({
    'ISBN13': isbn13s,
    'Price': prices,
    'Title': titles,
    'Author': authors,
    'Publisher': publishers,
    'Year': years,
    'Binding': bindings,
    'Image_Link': image_links
})

# Define the file name
file_name = 'books_data23.tsv'

# Export DataFrame to TSV file
df.to_csv(file_name, sep='\t', index=False)
print("Data scraped successfully and saved in 'books_data.tsv'.")

print("Processing complete. Check the generated files.")

Lines 210501 to 212600 extracted and saved to file.txt


100%|██████████| 2100/2100 [37:50<00:00,  1.08s/it]


Data scraped successfully and saved in 'books_data.tsv'.
Processing complete. Check the generated files.


second project

In [ ]:
import requests
from bs4 import BeautifulSoup
from tqdm import tqdm
import pandas as pd
import re
import time

def extract_lines(input_file_path, start_line, end_line, output_file_path):
    try:
        with open(input_file_path, 'r') as input_file, open(output_file_path, 'w') as output_file:
            lines = input_file.readlines()
            # Adjusting start_line and end_line to be within the valid range
            start_line = max(1, min(start_line, len(lines)))
            end_line = max(start_line, min(end_line, len(lines)))

            # Writing the selected lines to the output file
            output_file.writelines(lines[start_line - 1:end_line])

        print(f"Lines {start_line} to {end_line} extracted and saved to {output_file_path}")

    except Exception as e:
        print(f"Error: {e}")

def scrape_process(urls):
    for url in tqdm(urls):
      try:
        headers = {"User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/124.0.0.0 Safari/537.36"}
        response = requests.get(url.strip(), headers=headers)

        if not response.ok:
            print('Status Code:', response.status_code)
            if response.status_code == 429:
              time.sleep(60)
            else:
              time.sleep(5)
            with open('errors.txt', 'a') as error_file:
              error_file.write(url + '\n')
            raise Exception('Failed to fetch')
        time.sleep(0.1)
        soup = BeautifulSoup(response.text, 'html.parser')
        results_area = soup.find('div', class_='results-area')
        res = results_area.find_all('li', class_='product-item--row js_item_root')
        for r in res:
          price = r.find('div', "product-delivery").text.strip()
          if 'in huis' in price:
            # Find the <a> tag with the specific class
            a_tag = soup.find('a', class_='product-title px_list_page_product_click list_page_product_tracking_target')

            # Extract the href attribute
            if a_tag:
                href_value = a_tag.get('href')
                with open('hrefs95.txt', 'a') as href_file:
                    href_file.write('https://www.bol.com/' + href_value + '\n')
      except Exception as e:
        continue

extract_lines('Bottom.txt', 877001, 890000, 'file.txt')

# Read URLs from file
with open('file.txt', 'r') as file:
    urls = file.readlines()
scrape_process(urls)

Lines 877001 to 884459 extracted and saved to file.txt


 91%|█████████ | 6805/7459 [1:20:42<07:40,  1.42it/s]

Status Code: 404


100%|██████████| 7459/7459 [1:28:43<00:00,  1.40it/s]


3rd project: find 4 digit and 5 digit prices.

In [ ]:
import requests
from bs4 import BeautifulSoup
from tqdm import tqdm
import pandas as pd
import re
import time
import random

def extract_lines(input_file_path, start_line, end_line, output_file_path):
    try:
        with open(input_file_path, 'r') as input_file, open(output_file_path, 'w') as output_file:
            lines = input_file.readlines()
            # Adjusting start_line and end_line to be within the valid range
            start_line = max(1, min(start_line, len(lines)))
            end_line = max(start_line, min(end_line, len(lines)))

            # Writing the selected lines to the output file
            output_file.writelines(lines[start_line - 1:end_line])

        print(f"Lines {start_line} to {end_line} extracted and saved to {output_file_path}")

    except Exception as e:
        print(f"Error: {e}")

def check_results(url):
  with open('exceptions.txt', 'a') as file_er:
    try:
        headers = {"User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/124.0.0.0 Safari/537.36"}
        response = requests.get(url, headers=headers)

        if not response.ok:
            print('Status Code:', response.status_code)
            if response.status_code == 429:
              time.sleep(0.1)
            else:
              time.sleep(0.05)
            raise Exception('Failed to fetch')
        #time.sleep(random.uniform(0.3, 0.6))
        soup = BeautifulSoup(response.text, 'html.parser')
        ul = soup.find('ul', id="srp-results")
        if not ul:
          time.sleep(1)
          return
        li = ul.find('li', class_="cf result-item")
        isbn13=""
        price=""
        isbn_data = li.find('p', class_="isbn pub-data")
        if isbn_data:
            isbn13 = isbn_data.find('span', class_="pl-md")
            if isbn13:
                isbn13 = isbn13.text.strip()
                isbn13 = isbn13.replace('ISBN 13: ', '')
        if isbn13=="":
            isbn13 = str(url.split('/')[-1])
        price = li.find('p', class_="item-price")
        if price:
            # Extract the numerical part of the price and convert it to an integer
            price = int(re.search(r'\d+', price.text.strip().replace(",", "")).group())
        if price>=10000:
          line = "#ISBN#" + str(isbn13) + "#Price#" + str(price) + "#"
          with open('morethan10k.txt', 'a') as file1:
            file1.write(line +'\n')
        elif price >= 5000:
          line = "#ISBN#" + str(isbn13) + "#Price#" + str(price) + "#"
          with open('Errors.txt', 'a') as file2:
            file2.write(line +'\n')
        elif price >=100:
          if price >=1000:
            line = "#ISBN#" + str(isbn13) + "#Price#" + str(price) + "#"
          else:
            line = "#ISBN#" + str(isbn13) + "#Price#0" + str(price) + "#"
          with open('Hundreds.txt', 'a') as file3:
            file3.write(line +'\n')


    except Exception as e:
      print("Error on URL:", url, "Error:", e)
      file_er.write(url +'\n')
      time.sleep(0.1)


extract_lines('Last_Check_5000.txt', 0, 10000, 'file.txt')

# Read URLs from file
with open('file.txt', 'r') as file:
    urls = file.readlines()

for url in tqdm(urls):
    url = url.strip()  # Remove leading/trailing whitespace and newline characters
    check_results(url)
    time.sleep(0.1)

Lines 1 to 10000 extracted and saved to file.txt


  1%|          | 83/10000 [01:00<2:04:25,  1.33it/s]

Status Code: 429
Error on URL: https://www.abebooks.com/book-search/isbn/9780006344186 Error: Failed to fetch


  1%|          | 89/10000 [01:05<2:13:13,  1.24it/s]

Status Code: 429
Error on URL: https://www.abebooks.com/book-search/isbn/9780006371687 Error: Failed to fetch


...

 82%|████████▏ | 8224/10000 [1:28:36<18:27,  1.60it/s]

Status Code: 429
Error on URL: https://www.abebooks.com/book-search/isbn/9780671026424 Error: Failed to fetch


 82%|████████▏ | 8225/10000 [1:28:36<18:21,  1.61it/s]

Status Code: 429
Error on URL: https://www.abebooks.com/book-search/isbn/9780671026493 Error: Failed to fetch


 82%|████████▏ | 8226/10000 [1:28:37<18:16,  1.62it/s]